<a href="https://colab.research.google.com/github/abarb2022/Walmart-Recruiting---Store-Sales-Forecasting/blob/main/model_experiment_prophet.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Downloading Kaggle data sets directly into Colab**

Install the kaggle python library

In [ ]:
! pip install kaggle

Mount the Google drive so you can store your kaggle API credentials for future use

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


Make a directory for kaggle at the temporary instance location on Colab drive.

Download your kaggle API key (.json file). You can do this by going to your kaggle account page and clicking 'Create new API token' under the API section.

In [3]:
! mkdir ~/.kaggle

Upload the json file to Google Drive and then copy to the temporary location.

In [4]:
!cp /content/drive/MyDrive/ColabNotebooks/kaggle_API_credentials/kaggle.json ~/.kaggle/kaggle.json

Change the file permissions to read/write to the owner only

In [5]:
! chmod 600 ~/.kaggle/kaggle.json

**Competitions and Datasets are the two types of Kaggle data**

**1. Download competition data**

If you get 403 Forbidden error, you need to click 'Late Submission' on the Kaggle page for that competition.

In [6]:
! kaggle competitions download -c walmart-recruiting-store-sales-forecasting

  0% 0.00/2.70M [00:00<?, ?B/s]
100% 2.70M/2.70M [00:00<00:00, 699MB/s]


Unzip, in case the downloaded file is zipped. Refresh the files on the left hand side to update the view.

In [7]:
! unzip walmart-recruiting-store-sales-forecasting

Archive:  walmart-recruiting-store-sales-forecasting.zip
  inflating: features.csv.zip        
  inflating: sampleSubmission.csv.zip  
  inflating: stores.csv              
  inflating: test.csv.zip            
  inflating: train.csv.zip           


In [8]:
import pandas as pd
import numpy as np
from prophet import Prophet
import matplotlib.pyplot as plt
import holidays
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.pipeline import Pipeline
from sklearn.metrics import mean_absolute_error
import gc
import joblib
import os
from datetime import datetime
import json
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.expand_frame_repr', False)

In [9]:

stores = pd.read_csv('stores.csv')
train = pd.read_csv("train.csv.zip")
features = pd.read_csv('features.csv.zip')
sample = pd.read_csv('sampleSubmission.csv.zip')
test = pd.read_csv('test.csv.zip')

In [10]:
# Convert 'Date' columns to datetime objects for easier manipulation
train['Date'] = pd.to_datetime(train['Date'])
test['Date'] = pd.to_datetime(test['Date'])
features['Date'] = pd.to_datetime(features['Date'])

# Merge features with train and test data.
# Note: 'IsHoliday' is present in both train/test and features.csv.
# We'll merge on it to ensure consistency, but if there were discrepancies,
# we'd need a more careful merge strategy.
train_df = pd.merge(train, features, on=['Store', 'Date', 'IsHoliday'], how='left')
test_df = pd.merge(test, features, on=['Store', 'Date', 'IsHoliday'], how='left')

# Merge store information
train_df = pd.merge(train_df, stores, on='Store', how='left')
test_df = pd.merge(test_df, stores, on='Store', how='left')

print("\n--- Merged Train Data Head ---")
print(train_df.head())
print("\n--- Merged Test Data Head ---")
print(test_df.head())

print("\n--- Merged Train Data Info ---")
print(train_df.info())
print("\n--- Merged Test Data Info ---")
print(test_df.info())

# Free up memory
del train, test, features, stores
gc.collect()


--- Merged Train Data Head ---
   Store  Dept       Date  Weekly_Sales  IsHoliday  Temperature  Fuel_Price  MarkDown1  MarkDown2  MarkDown3  MarkDown4  MarkDown5         CPI  Unemployment Type    Size
0      1     1 2010-02-05      24924.50      False        42.31       2.572        NaN        NaN        NaN        NaN        NaN  211.096358         8.106    A  151315
1      1     1 2010-02-12      46039.49       True        38.51       2.548        NaN        NaN        NaN        NaN        NaN  211.242170         8.106    A  151315
2      1     1 2010-02-19      41595.55      False        39.93       2.514        NaN        NaN        NaN        NaN        NaN  211.289143         8.106    A  151315
3      1     1 2010-02-26      19403.54      False        46.63       2.561        NaN        NaN        NaN        NaN        NaN  211.319643         8.106    A  151315
4      1     1 2010-03-05      21827.90      False        46.50       2.625        NaN        NaN        NaN        Na

0

## **DATA CLEANING**


In [11]:
class MissingValueImputer(BaseEstimator, TransformerMixin):
    """
    Custom Transformer to handle missing values for specific columns.
    - MarkDown columns: fill with 0.
    - Other specified numerical columns: fill with ffill then bfill, fallback to mean.
    """
    def __init__(self, markdown_cols=None, numerical_cols_to_impute=None):
        self.markdown_cols = markdown_cols if markdown_cols is not None else [f'MarkDown{i}' for i in range(1, 6)]
        self.numerical_cols_to_impute = numerical_cols_to_impute if numerical_cols_to_impute is not None else ['Temperature', 'Fuel_Price', 'CPI', 'Unemployment']
        self.means = {} # To store means for fallback imputation during transform

    def fit(self, X, y=None):
        # Calculate means for fallback imputation from the training data
        for col in self.numerical_cols_to_impute:
            if col in X.columns:
                self.means[col] = X[col].mean()
        return self

    def transform(self, X):
        X_copy = X.copy()


        for col in self.markdown_cols:
          if col in X_copy.columns:
            X_copy[f"{col}_was_missing"] = X_copy[col].isna().astype(int)
            X_copy[col] = X_copy[col].fillna(0)


        # Impute other numerical columns with ffill then bfill, fallback to mean
        for col in self.numerical_cols_to_impute:
            if col in X_copy.columns:
                X_copy[col] = X_copy[col].fillna(method='ffill').fillna(method='bfill')
                # Fallback to mean if NaNs still exist (e.g., if all values were NaN in a column)
                if X_copy[col].isnull().any() and col in self.means:
                    X_copy[col] = X_copy[col].fillna(self.means[col])
        return X_copy

In [12]:
class DateFeatureExtractor(BaseEstimator, TransformerMixin):
    """
    Custom Transformer to extract temporal features from the 'Date' column.
    """
    def __init__(self, date_column='Date'):
        self.date_column = date_column

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        X_copy = X.copy()
        if self.date_column not in X_copy.columns:
            raise ValueError(f"Date column '{self.date_column}' not found in DataFrame.")

        X_copy[self.date_column] = pd.to_datetime(X_copy[self.date_column])

        X_copy['Year'] = X_copy[self.date_column].dt.year
        X_copy['Month'] = X_copy[self.date_column].dt.month
        X_copy['Month_sin'] = np.sin(2 * np.pi * X_copy['Month'] / 12)
        X_copy['Month_cos'] = np.cos(2 * np.pi * X_copy['Month'] / 12)

        # Using .dt.isocalendar().week for consistent week numbering across years
        X_copy['Week'] = X_copy[self.date_column].dt.isocalendar().week.astype(int)
        X_copy['Day'] = X_copy[self.date_column].dt.day
        X_copy['DayOfWeek'] = X_copy[self.date_column].dt.dayofweek

        # Convert IsHoliday to integer if it exists and is boolean
        if 'IsHoliday' in X_copy.columns and X_copy['IsHoliday'].dtype == bool:
            X_copy['IsHoliday'] = X_copy['IsHoliday'].astype(int)

        return X_copy.drop(columns=[ "Month"]) # Drop the original Date column


In [13]:
class CategoricalFeatureConverter(BaseEstimator, TransformerMixin):
    """
    Custom Transformer to convert specified columns to 'category' dtype
    for LightGBM to handle them efficiently.
    """
    def __init__(self, categorical_cols=None):
        self.categorical_cols = categorical_cols if categorical_cols is not None else ['Store', 'Dept', 'Type']

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        X_copy = X.copy()
        for col in self.categorical_cols:
            if col in X_copy.columns:
                X_copy[col] = X_copy[col].astype('category')
        return X_copy

In [14]:
# Define specific Walmart holidays based on the competition description
def get_walmart_holidays():
    holiday_dates = pd.DataFrame(columns=['ds', 'holiday'])

    # Super Bowl
    super_bowl = ['2010-02-12', '2011-02-11', '2012-02-10', '2013-02-08']
    holiday_dates = pd.concat([holiday_dates, pd.DataFrame({
        'ds': pd.to_datetime(super_bowl),
        'holiday': 'Super Bowl'
    })])

    # Labor Day
    labor_day = ['2010-09-10', '2011-09-09', '2012-09-07', '2013-09-06']
    holiday_dates = pd.concat([holiday_dates, pd.DataFrame({
        'ds': pd.to_datetime(labor_day),
        'holiday': 'Labor Day'
    })])

    # Thanksgiving
    thanksgiving = ['2010-11-26', '2011-11-25', '2012-11-23', '2013-11-29']
    holiday_dates = pd.concat([holiday_dates, pd.DataFrame({
        'ds': pd.to_datetime(thanksgiving),
        'holiday': 'Thanksgiving'
    })])

    # Christmas
    christmas = ['2010-12-31', '2011-12-30', '2012-12-28', '2013-12-27']
    holiday_dates = pd.concat([holiday_dates, pd.DataFrame({
        'ds': pd.to_datetime(christmas),
        'holiday': 'Christmas'
    })])

    return holiday_dates

walmart_holidays = get_walmart_holidays()

/tmp/ipython-input-14-4289254921.py:7: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  holiday_dates = pd.concat([holiday_dates, pd.DataFrame({


In [ ]:
# Install required packages
!pip install prophet holidays joblib

In [15]:


y_train = train_df['Weekly_Sales']
X_train = train_df.drop(columns=['Weekly_Sales', 'Id'], errors='ignore')

temp_train_df = X_train.copy()
temp_train_df['Date'] = pd.to_datetime(train_df['Date']) # Get original dates back for sorting
temp_train_df['Weekly_Sales'] = y_train

temp_train_df = temp_train_df.sort_values(by='Date').reset_index(drop=True)

# Define a cutoff date for validation
validation_cutoff_date = pd.to_datetime('2012-09-01')

X_train_split = temp_train_df[temp_train_df['Date'] < validation_cutoff_date]
y_train_split = temp_train_df[temp_train_df['Date'] < validation_cutoff_date]['Weekly_Sales']

X_val_split = temp_train_df[temp_train_df['Date'] >= validation_cutoff_date]
y_val_split = temp_train_df[temp_train_df['Date'] >= validation_cutoff_date]['Weekly_Sales']

preprocessing_pipeline = Pipeline([
    ('date_extractor', DateFeatureExtractor()),
    ('missing_imputer', MissingValueImputer()),
    ('cat_converter', CategoricalFeatureConverter())
])

X_train_processed = preprocessing_pipeline.fit_transform(X_train_split)
X_val_processed = preprocessing_pipeline.transform(X_val_split)

# Add Weekly_Sales back to processed data
X_train_processed['Weekly_Sales'] = y_train_split.values
X_val_processed['Weekly_Sales'] = y_val_split.values



def weighted_mean_absolute_error(y_true, y_pred, weights):
    return np.sum(weights * np.abs(y_true - y_pred)) / np.sum(weights)

val_weights = np.where(X_val_split['IsHoliday'] == 1, 5, 1)

log_data = {

    'total_combinations': 0,
    'models_trained': 0,
    'models_skipped': 0,
    'validation_metrics': {}
}

/tmp/ipython-input-11-1027183038.py:32: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  X_copy[col] = X_copy[col].fillna(method='ffill').fillna(method='bfill')
/tmp/ipython-input-11-1027183038.py:32: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  X_copy[col] = X_copy[col].fillna(method='ffill').fillna(method='bfill')
/usr/local/lib/python3.11/dist-packages/sklearn/pipeline.py:62: FutureWarning: This Pipeline instance is not fitted yet. Call 'fit' with appropriate arguments before using other methods such as transform, predict, etc. This will raise an error in 1.8 instead of the current warning.
  warnings.warn(


# appr 2


In [19]:
def get_nearest_dept(store, dept, X_train_processed):
    """Find department in same store with closest average sales"""
    store_data = X_train_processed[X_train_processed['Store'] == store]
    if len(store_data) == 0:
        return None

    # Convert Dept to numeric if it's categorical
    dept_means = store_data.copy()
    dept_means['Dept'] = pd.to_numeric(dept_means['Dept'], errors='coerce')
    dept = pd.to_numeric(dept, errors='coerce')

    # Calculate mean sales per department in this store
    dept_means = dept_means.groupby('Dept')['Weekly_Sales'].mean().reset_index()
    dept_means['abs_diff'] = np.abs(dept_means['Dept'] - dept)

    # Return the closest department (by ID) with enough data
    nearest = dept_means.sort_values(['abs_diff', 'Weekly_Sales']).iloc[0]
    return nearest['Dept']

In [37]:
def train_models(X_train_processed, X_val_processed):
    """Train Prophet models for each store-dept combination with fallbacks"""
    # Initialize logging and storage
    log_data = {
        'total_combinations': 0,
        'models_trained': 0,
        'models_skipped': 0,
        'fallback_used': 0,
        'validation_metrics': {}
    }

    combinations = X_train_processed[['Store', 'Dept']].drop_duplicates()
    log_data['total_combinations'] = len(combinations)
    val_results = []
    models = {}  # Store trained models by (Store, Dept)

    # Define regressors
    extra_regressors = ['Temperature', 'Fuel_Price', 'CPI', 'Unemployment',
                      'IsHoliday', 'Size', 'MarkDown1', 'MarkDown2',
                      'MarkDown3', 'MarkDown4', 'MarkDown5']

    # 1. First train global fallback model
    print("\nTraining global fallback model...")
    prophet_train_global = X_train_processed[['Date', 'Weekly_Sales'] + extra_regressors].rename(columns={
        'Date': 'ds',
        'Weekly_Sales': 'y'
    })

    model_global = Prophet(
        holidays=walmart_holidays,
        yearly_seasonality=True,
        weekly_seasonality=True,
        daily_seasonality=False,
        seasonality_mode='multiplicative'
    )

    for regressor in extra_regressors:
        if regressor in prophet_train_global.columns:
            model_global.add_regressor(regressor)

    model_global.fit(prophet_train_global)
    print("Global fallback model trained.")

    # 2. Train individual store-dept models
    print(f"\nStarting training on {len(X_train_processed):,} samples")
    print(f"Found {len(combinations)} unique store-dept combinations")

    for idx, (store, dept) in enumerate(combinations.itertuples(index=False), 1):
        print(f"\nProcessing {idx}/{len(combinations)} - Store {store}, Dept {dept}")
        print("-" * 50)

        # Filter data for this store-dept combination
        train_data = X_train_processed[(X_train_processed['Store'] == store) &
                                     (X_train_processed['Dept'] == dept)]
        val_data = X_val_processed[(X_val_processed['Store'] == store) &
                                 (X_val_processed['Dept'] == dept)]

        if len(train_data) < 10:
            print(f"  Skipping - only {len(train_data)} training samples")
            log_data['models_skipped'] += 1
            continue

        # Prepare Prophet data
        prophet_train = train_data[['Date', 'Weekly_Sales'] + extra_regressors].rename(columns={
            'Date': 'ds',
            'Weekly_Sales': 'y'
        })

        # Initialize and train Prophet model
        model = Prophet(
            holidays=walmart_holidays,
            yearly_seasonality=True,
            weekly_seasonality=True,
            daily_seasonality=False,
            seasonality_mode='multiplicative'
        )

        for regressor in extra_regressors:
            if regressor in prophet_train.columns:
                model.add_regressor(regressor)

        print(f"  Training on {len(prophet_train)} samples...")
        model.fit(prophet_train)
        models[(store, dept)] = model  # Store the trained model
        log_data['models_trained'] += 1

        # Validate if validation data exists
        if len(val_data) > 0:
            prophet_val = val_data[['Date'] + extra_regressors].rename(columns={'Date': 'ds'})
            forecast = model.predict(prophet_val)

            # Calculate metrics
            val_actual = val_data['Weekly_Sales'].values
            val_pred = forecast['yhat'].values
            val_weights = np.where(val_data['IsHoliday'] == 1, 5, 1)

            mae = mean_absolute_error(val_actual, val_pred)
            wmae = weighted_mean_absolute_error(val_actual, val_pred, val_weights)

            val_results.append({
                'Store': store,
                'Dept': dept,
                'Date': val_data['Date'].values,
                'Actual': val_actual,
                'Predicted': val_pred,
                'MAE': mae,
                'WMAE': wmae,
                'IsHoliday': val_data['IsHoliday'].values,
                'UsedFallback': False
            })

            print(f"  Validation MAE: {mae:.2f}, WMAE: {wmae:.2f}")

    # 3. Handle skipped combinations using fallbacks
    skipped_combinations = set(combinations.itertuples(index=False)) - set(models.keys())
    for store, dept in skipped_combinations:

        print(f"\nProcessing skipped combination - Store {store}, Dept {dept}")
        val_data = X_val_processed[(X_val_processed['Store'] == store) &
                                 (X_val_processed['Dept'] == dept)]

        if len(val_data) == 0:
            continue

        # Try nearest neighbor fallback first
        nearest_dept = get_nearest_dept(store, dept, X_train_processed)
        if nearest_dept is not None and (store, nearest_dept) in models:
            print(f"  Using nearest neighbor: Store {store}, Dept {nearest_dept}")
            model = models[(store, nearest_dept)]
            fallback_type = "nearest_neighbor"
        else:
            print("  Using global fallback model")
            model = model_global
            fallback_type = "global"

        prophet_val = val_data[['Date'] + extra_regressors].rename(columns={'Date': 'ds'})
        forecast = model.predict(prophet_val)

        val_actual = val_data['Weekly_Sales'].values
        val_pred = forecast['yhat'].values
        val_weights = np.where(val_data['IsHoliday'] == 1, 5, 1)

        mae = mean_absolute_error(val_actual, val_pred)
        wmae = weighted_mean_absolute_error(val_actual, val_pred, val_weights)

        val_results.append({
            'Store': store,
            'Dept': dept,
            'Date': val_data['Date'].values,
            'Actual': val_actual,
            'Predicted': val_pred,
            'MAE': mae,
            'WMAE': wmae,
            'IsHoliday': val_data['IsHoliday'].values,
            'UsedFallback': True,
            'FallbackType': fallback_type
        })

        log_data['fallback_used'] += 1
        print(f"  Fallback Validation MAE: {mae:.2f}, WMAE: {wmae:.2f}")

    return models, model_global, val_results, log_data


In [38]:
models, model_global, val_results, log_data = train_models(X_train_processed, X_val_processed)



Training global fallback model...


DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/pk4koakx.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/g77iaj_f.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.11/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=51431', 'data', 'file=/tmp/tmpe9dat84c/pk4koakx.json', 'init=/tmp/tmpe9dat84c/g77iaj_f.json', 'output', 'file=/tmp/tmpe9dat84c/prophet_modellncu9t2y/prophet_model-20250706190343.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
19:03:43 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
19:06:15 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing
DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/gsxu_705.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/kf53vlur.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/

Global fallback model trained.

Starting training on 397,841 samples
Found 3326 unique store-dept combinations

Processing 1/3326 - Store 1, Dept 1
--------------------------------------------------
  Training on 135 samples...
  Validation MAE: 3912.91, WMAE: 2760.60

Processing 2/3326 - Store 29, Dept 5
--------------------------------------------------
  Training on 135 samples...


DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/9k8dsfq0.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/5ws42gfa.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.11/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=80327', 'data', 'file=/tmp/tmpe9dat84c/9k8dsfq0.json', 'init=/tmp/tmpe9dat84c/5ws42gfa.json', 'output', 'file=/tmp/tmpe9dat84c/prophet_model4z1hkosi/prophet_model-20250706190617.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
19:06:17 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
19:06:17 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing
DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/4_5iyo6o.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/wpyjsyn_.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/

  Validation MAE: 2879.08, WMAE: 2215.29

Processing 3/3326 - Store 29, Dept 6
--------------------------------------------------
  Training on 135 samples...


...

  Validation MAE: 1187.15, WMAE: 829.84

Processing 3305/3326 - Store 9, Dept 78
--------------------------------------------------
  Skipping - only 2 training samples

Processing 3306/3326 - Store 8, Dept 96
--------------------------------------------------
  Skipping - only 3 training samples

Processing 3307/3326 - Store 38, Dept 99
--------------------------------------------------
  Skipping - only 1 training samples

Processing 3308/3326 - Store 37, Dept 99
--------------------------------------------------
  Skipping - only 2 training samples

Processing 3309/3326 - Store 21, Dept 50
--------------------------------------------------
  Skipping - only 1 training samples

Processing 3310/3326 - Store 30, Dept 19
--------------------------------------------------
  Skipping - only 1 training samples

Processing 3311/3326 - Store 33, Dept 32
--------------------------------------------------
  Training on 27 samples...


20:31:36 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing
INFO:prophet:n_changepoints greater than number of observations. Using 18.
DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/jwiamcfs.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpe9dat84c/80adoigc.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.11/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=24131', 'data', 'file=/tmp/tmpe9dat84c/jwiamcfs.json', 'init=/tmp/tmpe9dat84c/80adoigc.json', 'output', 'file=/tmp/tmpe9dat84c/prophet_model1x5jeuku/prophet_model-20250706203136.csv', 'method=optimize', 'algorithm=newton', 'iter=10000']
20:31:36 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing


  Validation MAE: 288572.77, WMAE: 288572.77

Processing 3312/3326 - Store 45, Dept 96
--------------------------------------------------
  Skipping - only 1 training samples

Processing 3313/3326 - Store 44, Dept 26
--------------------------------------------------
  Training on 24 samples...


20:31:55 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


  Validation MAE: 4118.47, WMAE: 3656.55

Processing 3314/3326 - Store 36, Dept 36
--------------------------------------------------
  Skipping - only 1 training samples

Processing 3315/3326 - Store 7, Dept 99
--------------------------------------------------
  Skipping - only 1 training samples

Processing 3316/3326 - Store 3, Dept 83
--------------------------------------------------
  Skipping - only 1 training samples

Processing 3317/3326 - Store 33, Dept 49
--------------------------------------------------
  Skipping - only 2 training samples

Processing 3318/3326 - Store 16, Dept 99
--------------------------------------------------
  Skipping - only 1 training samples

Processing 3319/3326 - Store 33, Dept 99
--------------------------------------------------
  Skipping - only 3 training samples

Processing 3320/3326 - Store 36, Dept 99
--------------------------------------------------
  Skipping - only 1 training samples

Processing 3321/3326 - Store 15, Dept 99
---------

In [39]:
# Calculate overall metrics
if val_results:
    # Create DataFrame from validation results
    all_rows = []
    for x in val_results:
        # Ensure all arrays are numpy arrays and have same length
        dates = np.array(x['Date'])
        actuals = np.array(x['Actual'])
        preds = np.array(x['Predicted'])
        is_holidays = np.array(x['IsHoliday'])

        # Handle case where arrays might have different lengths
        min_length = min(len(dates), len(actuals), len(preds), len(is_holidays))

        for i in range(min_length):
            all_rows.append({
                'Store': x['Store'],
                'Dept': x['Dept'],
                'Date': dates[i],
                'Actual': float(actuals[i]),  # Explicit conversion to float
                'Predicted': float(preds[i]),  # Explicit conversion to float
                'IsHoliday': bool(is_holidays[i]),  # Explicit conversion to bool
                'UsedFallback': x.get('UsedFallback', False),
                'FallbackType': x.get('FallbackType', None)
            })

    all_val = pd.DataFrame(all_rows)

    # Calculate weights - ensure IsHoliday is boolean
    all_val['Weight'] = np.where(all_val['IsHoliday'], 5, 1)

    # Calculate metrics with type safety
    try:
        overall_wmae = weighted_mean_absolute_error(
            all_val['Actual'].astype(float),
            all_val['Predicted'].astype(float),
            all_val['Weight'].astype(float))

        avg_mae = np.mean([float(x['MAE']) for x in val_results])
        avg_wmae = np.mean([float(x['WMAE']) for x in val_results])

        log_data['validation_metrics'] = {
            'overall_wmae': float(overall_wmae),
            'average_mae': float(avg_mae),
            'average_wmae': float(avg_wmae),
            'num_validated': int(len(all_val)),
            'coverage': float(len(all_val) / len(X_val_processed)),
            'fallback_usage': float(len(all_val[all_val['UsedFallback']]) / len(all_val))
        }

        print("\nOverall Validation Metrics:")
        print(f"- Weighted MAE (WMAE): {overall_wmae:.2f}")
        print(f"- Average MAE: {avg_mae:.2f}")
        print(f"- Average WMAE: {avg_wmae:.2f}")
        print(f"- Coverage: {len(all_val)/len(X_val_processed):.2%}")
        print(f"- Fallback Usage: {len(all_val[all_val['UsedFallback']])/len(all_val):.2%}")

        # Save results with type consistency
        all_val.to_csv('validation_results.csv', index=False)
        print("\nSaved validation results to validation_results.csv")

    except Exception as e:
        print(f"Error calculating metrics: {str(e)}")
        # Fallback to simple metrics if detailed calculation fails
        log_data['validation_metrics'] = {
            'error': str(e),
            'num_validated': len(all_val)
        }

# Save logs with error handling
try:
    with open('training_log.json', 'w') as f:
        json.dump(log_data, f, indent=2, default=str)  # Handle non-serializable types
    print("\nSaved training logs to training_log.json")
except Exception as e:
    print(f"Error saving logs: {str(e)}")

print("\nTraining and validation complete!")
print(f"- Models trained: {log_data.get('models_trained', 'N/A')}")
print(f"- Models skipped: {log_data.get('models_skipped', 'N/A')}")
print(f"- Fallbacks used: {log_data.get('fallback_used', 'N/A')}")
print(f"- Validation coverage: {len(all_val)/len(X_val_processed):.2%}" if 'all_val' in locals() else "N/A")


Overall Validation Metrics:
- Weighted MAE (WMAE): 2993.93
- Average MAE: 3320.07
- Average WMAE: 3395.95
- Coverage: 99.96%
- Fallback Usage: 0.18%

Saved validation results to validation_results.csv

Saved training logs to training_log.json

Training and validation complete!
- Models trained: 3161
- Models skipped: 165
- Fallbacks used: 19
- Validation coverage: 99.96%


In [34]:
!pip install mlflow

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.7/24.7 MB 30.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 38.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 242.7/242.7 kB 16.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 147.8/147.8 kB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.9/114.9 kB 9.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.0/85.0 kB 4.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 733.8/733.8 kB 22.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 65.8/65.8 kB 4.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.5/118.5 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.2/196.2 kB 11.0 MB/s eta 0:00:00


In [40]:

import dagshub, mlflow
# Try to get credentials from environment first
dagshub.init(
    repo_owner='abarb22',
    repo_name='Walmart-Recruiting---Store-Sales-Forecasting',
    mlflow=True
)

mlflow.set_experiment("Prophet_Training")


Initialized MLflow to track repo "abarb22/Walmart-Recruiting---Store-Sales-Forecasting"

Repository abarb22/Walmart-Recruiting---Store-Sales-Forecasting initialized!

<Experiment: artifact_location='mlflow-artifacts:/6d191f25b50a4e7fb678c9df08d0b2c9', creation_time=1751757513529, experiment_id='7', last_update_time=1751757513529, lifecycle_stage='active', name='Prophet_Training', tags={}>

In [ ]:
with mlflow.start_run(run_name="Prophet_Data_Cleaning"):
    # Log data cleaning parameters
    mlflow.log_param("missing_value_strategy", "MarkDowns->0, others->ffill/bfill/mean")
    mlflow.log_param("date_features_extracted", True)


    # After cleaning, log metrics about data quality
    mlflow.log_metric("train_samples", len(train_df))
    mlflow.log_metric("missing_values_filled", train_df.isna().sum().sum())

🏃 View run Prophet_Data_Cleaning at: https://dagshub.com/abarb22/Walmart-Recruiting---Store-Sales-Forecasting.mlflow/#/experiments/7/runs/3cfea17c875c461f8e88d1a9178d2a42
🧪 View experiment at: https://dagshub.com/abarb22/Walmart-Recruiting---Store-Sales-Forecasting.mlflow/#/experiments/7


In [ ]:
with mlflow.start_run(run_name="Prophet_Feature_Engineering"):
    # Log feature engineering parameters
    mlflow.log_param("temporal_features", ["Year", "Month", "Week", "Day", "DayOfWeek"])
    mlflow.log_param("cyclical_features", ["Month_sin", "Month_cos"])

    # After feature engineering, log the new feature count
    mlflow.log_metric("total_features", len(X_train_processed.columns))

🏃 View run Prophet_Feature_Engineering at: https://dagshub.com/abarb22/Walmart-Recruiting---Store-Sales-Forecasting.mlflow/#/experiments/7/runs/62a1768022334cde908a1c5341ae2cc9
🧪 View experiment at: https://dagshub.com/abarb22/Walmart-Recruiting---Store-Sales-Forecasting.mlflow/#/experiments/7


In [36]:
with mlflow.start_run(run_name="Prophet_50_Model_Training") as run:
    # --- Parameters ---
    mlflow.log_param("total_combinations", log_data.get('total_combinations'))
    mlflow.log_param("models_trained", log_data.get('models_trained'))
    mlflow.log_param("models_skipped", log_data.get('models_skipped'))

    # --- Metrics ---
    metrics = log_data.get('validation_metrics', {})
    if metrics:
        mlflow.log_metric("overall_wmae", metrics.get("overall_wmae", 0.0))
        mlflow.log_metric("average_mae", metrics.get("average_mae", 0.0))
        mlflow.log_metric("average_wmae", metrics.get("average_wmae", 0.0))
        mlflow.log_metric("validation_coverage", metrics.get("coverage", 0.0))

    # --- Artifacts ---
    mlflow.log_artifact("validation_results.csv")
    mlflow.log_artifact("training_log.json")

    print(f"\n✅ MLflow logging complete: Run ID = {run.info.run_id}")


✅ MLflow logging complete: Run ID = d80584f7a60f4cc4b2965a7645721f5b
🏃 View run Prophet_50_Model_Training at: https://dagshub.com/abarb22/Walmart-Recruiting---Store-Sales-Forecasting.mlflow/#/experiments/7/runs/d80584f7a60f4cc4b2965a7645721f5b
🧪 View experiment at: https://dagshub.com/abarb22/Walmart-Recruiting---Store-Sales-Forecasting.mlflow/#/experiments/7


In [41]:
with mlflow.start_run(run_name="Prophet_Full_Model_Training_with_strategy") as run:
    # --- Parameters ---
    mlflow.log_param("total_combinations", log_data.get('total_combinations'))
    mlflow.log_param("models_trained", log_data.get('models_trained'))
    mlflow.log_param("models_skipped", log_data.get('models_skipped'))

    # NEW: Fallback strategy parameters
    mlflow.log_param("fallback_strategy", "global+nearest_neighbor")
    mlflow.log_param("min_samples_required", 10)  # Your threshold for skipping models

    # --- Metrics ---
    metrics = log_data.get('validation_metrics', {})
    if metrics:
        # Existing metrics
        mlflow.log_metric("overall_wmae", metrics.get("overall_wmae", 0.0))
        mlflow.log_metric("average_mae", metrics.get("average_mae", 0.0))
        mlflow.log_metric("average_wmae", metrics.get("average_wmae", 0.0))
        mlflow.log_metric("validation_coverage", metrics.get("coverage", 0.0))

        # NEW: Fallback performance metrics
        mlflow.log_metric("fallback_usage_pct", metrics.get("fallback_usage", 0.0)*100)
        mlflow.log_metric("global_fallback_count",
                         len(all_val[all_val['FallbackType'] == "global"]))
        mlflow.log_metric("neighbor_fallback_count",
                         len(all_val[all_val['FallbackType'] == "nearest_neighbor"]))

        # NEW: Comparative metrics
        if 'fallback_usage' in metrics and metrics['fallback_usage'] > 0:
            fallback_wmae = all_val[all_val['UsedFallback']]['Actual'].astype(float).mean()
            primary_wmae = all_val[~all_val['UsedFallback']]['Actual'].astype(float).mean()
            mlflow.log_metric("fallback_vs_primary_ratio", fallback_wmae/primary_wmae)

    # --- Artifacts ---
    mlflow.log_artifact("validation_results.csv")
    mlflow.log_artifact("training_log.json")

    # NEW: Log fallback examples
    if 'all_val' in locals():
        fallback_samples = all_val[all_val['UsedFallback']].head(10)
        fallback_samples.to_csv("fallback_examples.csv", index=False)
        mlflow.log_artifact("fallback_examples.csv")


    print(f"\n✅ MLflow logging complete: Run ID = {run.info.run_id}")


✅ MLflow logging complete: Run ID = 8675b07feca74bad85348ba99d38104c
🏃 View run Prophet_Full_Model_Training_with_strategy at: https://dagshub.com/abarb22/Walmart-Recruiting---Store-Sales-Forecasting.mlflow/#/experiments/7/runs/8675b07feca74bad85348ba99d38104c
🧪 View experiment at: https://dagshub.com/abarb22/Walmart-Recruiting---Store-Sales-Forecasting.mlflow/#/experiments/7
